## Import packages necessary to structure the data and compile the VGG16 model for 6 channel images

In [12]:
import rasterio
import numpy as np
import os
import re
import random
import shutil
from tqdm import tqdm

## Move files to structure the data with labels
### Pair the before and after images based on their names and merge them to create 6 channel Images
### Move the files with fire damage to the Damage labelled folders 

In [5]:
# Define the directories for source images and their destination folders
source_folders = [
    ("/Volumes/HD710PRO/Fire_and_Hurricane_Images/Fire/DividedData/RGB_DamageTiles", "/Volumes/HD710PRO/Fire_and_Hurricane_Images/Fire/DividedData/BeforeRGB_DamageTiles"),
    ("/Volumes/HD710PRO/Fire_and_Hurricane_Images/Fire/DividedData/HorFlip_afterRGBdamage", "/Volumes/HD710PRO/Fire_and_Hurricane_Images/Fire/DividedData/HorFlip_beforeRGBdamage"),
    ("/Volumes/HD710PRO/Fire_and_Hurricane_Images/Fire/DividedData/ROT90_afterRGBdamage", "/Volumes/HD710PRO/Fire_and_Hurricane_Images/Fire/DividedData/ROT90_beforeRGBdamage"),
    ("/Volumes/HD710PRO/Fire_and_Hurricane_Images/Fire/DividedData/ROT180_afterRGBdamage", "/Volumes/HD710PRO/Fire_and_Hurricane_Images/Fire/DividedData/ROT180_beforeRGBdamage"),
    ("/Volumes/HD710PRO/Fire_and_Hurricane_Images/Fire/DividedData/ROT270_afterRGBdamage", "/Volumes/HD710PRO/Fire_and_Hurricane_Images/Fire/DividedData/ROT270_beforeRGBdamage"),
    ("/Volumes/HD710PRO/Fire_and_Hurricane_Images/Fire/DividedData/VertFlip_afterRGBdamage", "/Volumes/HD710PRO/Fire_and_Hurricane_Images/Fire/DividedData/VertFlip_beforeRGBdamage")
]

destination_folders = {
    'test': "/Volumes/HD710PRO/Fire_and_Hurricane_Images/Fire/6channel/Test/Damage",
    'validation': "/Volumes/HD710PRO/Fire_and_Hurricane_Images/Fire/6channel/Validation/Damage",
    'training': "/Volumes/HD710PRO/Fire_and_Hurricane_Images/Fire/6channel/Training/Damage"
}

# Ensure destination directories exist
for path in destination_folders.values():
    os.makedirs(path, exist_ok=True)
    
# Define a function to extract specific name identifters be able to pair the before and after images

def extract_identifiers(filename):
    match = re.search(r'RGB_(After|Before)Fire(\d+)_tile_(\d+)_?(.*).tif$', filename)
    if match:
        return match.groups()[1:]  # Return identifiers (X, Y, modification after data augmentation) for matching
    return None

# Define a function to pair the images in the before and after folders
def find_pairs(after_folder, before_folder):
    after_files = {f: extract_identifiers(f) for f in os.listdir(after_folder) if f.endswith('.tif')}
    before_files = {f: extract_identifiers(f) for f in os.listdir(before_folder) if f.endswith('.tif')}
    
    pairs = []
    for af, a_ids in after_files.items():
        for bf, b_ids in before_files.items():
            if a_ids == b_ids:
                pairs.append((os.path.join(after_folder, af), os.path.join(before_folder, bf)))
    return pairs

#Define a function to merge the 3 Channel RGB paired images into one 6 Channel Image 

def create_and_save_6_channel_image(after_file_path, before_file_path, destination_path):
    with rasterio.open(after_file_path) as after_src, rasterio.open(before_file_path) as before_src:
        after_img = after_src.read()
        before_img = before_src.read()
        
        if after_img.shape[1:] == before_img.shape[1:]:
            six_channel_img = np.concatenate((before_img, after_img), axis=0)
            out_meta = after_src.meta
            out_meta.update(count=6)
            
            with rasterio.open(destination_path, 'w', **out_meta) as dest:
                dest.write(six_channel_img)
        else:
            print(f"Skipping due to size mismatch: {after_file_path} & {before_file_path}")

# Define a function to split the 6 Channel image data for training and testing ( 80% for training, 10% for validation, and 10% for testing) 
# Distribute the images into the labelled folder paths             
def distribute_images(pairs, test_path, validation_path, training_path):
    random.shuffle(pairs)
    total = len(pairs)
    test_count, validation_count = total // 10, total // 10

    for i, (after_path, before_path) in enumerate(pairs):
        if i < test_count:
            destination = os.path.join(test_path, os.path.basename(after_path).replace("AfterFire", "6Channel"))
        elif i < test_count + validation_count:
            destination = os.path.join(validation_path, os.path.basename(after_path).replace("AfterFire", "6Channel"))
        else:
            destination = os.path.join(training_path, os.path.basename(after_path).replace("AfterFire", "6Channel"))
        
        create_and_save_6_channel_image(after_path, before_path, destination)
        print(f"Progress: Completed {i+1} of {total} tasks")

# Use the functions to pair, merge, distribute and organize the data.
def main():
    print("Starting image pairing and distribution process.")
    for (after_folder, before_folder) in source_folders:
        print(f"Processing pairs from: {after_folder} and {before_folder}")
        pairs = find_pairs(after_folder, before_folder)
        print(f"Found {len(pairs)} pairs to process.")
        
        distribute_images(pairs, destination_folders['test'], destination_folders['validation'], destination_folders['training'])
    
    print("Image processing and distribution complete.")

if __name__ == "__main__":
    main()


Starting image pairing and distribution process.
Processing pairs from: /Volumes/HD710PRO/Fire_and_Hurricane_Images/Fire/DividedData/RGB_DamageTiles and /Volumes/HD710PRO/Fire_and_Hurricane_Images/Fire/DividedData/BeforeRGB_DamageTiles
Found 4847 pairs to process.
Progress: Completed 1 of 4847 tasks
Progress: Completed 2 of 4847 tasks
Progress: Completed 3 of 4847 tasks
Progress: Completed 4 of 4847 tasks
Progress: Completed 5 of 4847 tasks
Progress: Completed 6 of 4847 tasks
Progress: Completed 7 of 4847 tasks
Progress: Completed 8 of 4847 tasks
Progress: Completed 9 of 4847 tasks
Progress: Completed 10 of 4847 tasks
Progress: Completed 11 of 4847 tasks
Progress: Completed 12 of 4847 tasks
Progress: Completed 13 of 4847 tasks
Progress: Completed 14 of 4847 tasks
Progress: Completed 15 of 4847 tasks
Progress: Completed 16 of 4847 tasks
Progress: Completed 17 of 4847 tasks
Progress: Completed 18 of 4847 tasks
Progress: Completed 19 of 4847 tasks
Progress: Completed 20 of 4847 tasks
Prog

### Move the files with NO fire damage to the Undamaged labelled folders 

In [6]:
# Define the directories for source images and destination folders
source_folders = [
    ("/Volumes/HD710PRO/Fire_and_Hurricane_Images/Fire/DividedData/BeforeRGB_UndamagedTiles", "/Volumes/HD710PRO/Fire_and_Hurricane_Images/Fire/DividedData/AfterRGB_UndamagedTiles")
]

destination_folders = {
    'test': "/Volumes/HD710PRO/Fire_and_Hurricane_Images/Fire/6channel/Test/Undamaged",
    'validation': "/Volumes/HD710PRO/Fire_and_Hurricane_Images/Fire/6channel/Validation/Undamaged",
    'training': "/Volumes/HD710PRO/Fire_and_Hurricane_Images/Fire/6channel/Training/Undamaged"
}

# Use the functions to pair, merge, distribute and organize the data.

def main():
    print("Starting image pairing and distribution process.")
    for (after_folder, before_folder) in source_folders:
        print(f"Processing pairs from: {after_folder} and {before_folder}")
        pairs = find_pairs(after_folder, before_folder)
        print(f"Found {len(pairs)} pairs to process.")
        
        distribute_images(pairs, destination_folders['test'], destination_folders['validation'], destination_folders['training'])
    
    print("Image processing and distribution complete.")

if __name__ == "__main__":
    main()


Starting image pairing and distribution process.
Processing pairs from: /Volumes/HD710PRO/Fire_and_Hurricane_Images/Fire/DividedData/BeforeRGB_UndamagedTiles and /Volumes/HD710PRO/Fire_and_Hurricane_Images/Fire/DividedData/AfterRGB_UndamagedTiles
Found 77064 pairs to process.
Progress: Completed 1 of 77064 tasks
Progress: Completed 2 of 77064 tasks
Progress: Completed 3 of 77064 tasks
Progress: Completed 4 of 77064 tasks
Progress: Completed 5 of 77064 tasks
Progress: Completed 6 of 77064 tasks
Progress: Completed 7 of 77064 tasks
Progress: Completed 8 of 77064 tasks
Progress: Completed 9 of 77064 tasks
Progress: Completed 10 of 77064 tasks
Progress: Completed 11 of 77064 tasks
Progress: Completed 12 of 77064 tasks
Progress: Completed 13 of 77064 tasks
Progress: Completed 14 of 77064 tasks
Progress: Completed 15 of 77064 tasks
Progress: Completed 16 of 77064 tasks
Progress: Completed 17 of 77064 tasks
Progress: Completed 18 of 77064 tasks
Progress: Completed 19 of 77064 tasks
Progress: 

/opt/anaconda3/lib/python3.9/site-packages/rasterio/__init__.py:304: NotGeoreferencedWarning: Dataset has no geotransform, gcps, or rpcs. The identity matrix will be returned.
  dataset = DatasetReader(path, driver=driver, sharing=sharing, **kwargs)


Progress: Completed 68287 of 77064 tasks
Progress: Completed 68288 of 77064 tasks
Progress: Completed 68289 of 77064 tasks
Progress: Completed 68290 of 77064 tasks
Progress: Completed 68291 of 77064 tasks
Progress: Completed 68292 of 77064 tasks
Progress: Completed 68293 of 77064 tasks
Progress: Completed 68294 of 77064 tasks
Progress: Completed 68295 of 77064 tasks
Progress: Completed 68296 of 77064 tasks
Progress: Completed 68297 of 77064 tasks
Progress: Completed 68298 of 77064 tasks
Progress: Completed 68299 of 77064 tasks
Progress: Completed 68300 of 77064 tasks
Progress: Completed 68301 of 77064 tasks
Progress: Completed 68302 of 77064 tasks
Progress: Completed 68303 of 77064 tasks
Progress: Completed 68304 of 77064 tasks
Progress: Completed 68305 of 77064 tasks
Progress: Completed 68306 of 77064 tasks
Progress: Completed 68307 of 77064 tasks
Progress: Completed 68308 of 77064 tasks
Progress: Completed 68309 of 77064 tasks
Progress: Completed 68310 of 77064 tasks
Progress: Comple